In [1]:
# conda install scikit-learn
# install from: http://docs.python-requests.org/en/master/
# to fix ssl installation of python packages issue
# curl https://bootstrap.pypa.io/get-pip.py | python3
# instructions to setup virtualenv
# https://www.tensorflow.org/install/install_mac
# pip3 install -r requirements.txt
# https://www.datacamp.com/community/tutorials/tensorflow-tutorial
# https://github.com/jtopor/CUNY-MSDA-661/blob/master/CIFAR-100/TF-Layers-CIFAR-100-v2.py

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import requests
import cv2
import h5py
import scipy.misc
import numpy as np
import csv
import sklearn.model_selection as model
import pickle 
import tensorflow as tf

from csv import DictReader
from urllib.request import urlopen
from matplotlib.pyplot import imshow
from fr_utils import *
from inception_blocks_v2 import *
from skimage import transform
from tensorflow.contrib import learn
from tensorflow.contrib.learn.python.learn.estimators import model_fn as model_fn_lib

%matplotlib inline
%load_ext autoreload
%autoreload

learning_rate = 0.001

np.set_printoptions(threshold=np.nan)

/Library/Frameworks/Python.framework/Versions/3.5/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: compiletime version 3.6 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.5
  return f(*args, **kwds)
Using TensorFlow backend.


In [2]:
def convert_input_format(data):    
    return np.transpose(
        np.reshape(data, (-1, 32, 32, 3), order="F"),
        axes=(0, 2, 1, 3)
    )

def convert_output_labels(data):
    return np.asarray(data['fine_labels'], dtype=np.int32)

def one_hot_labels(labels):
    return tf.one_hot(indices=tf.cast(labels, tf.int32), depth=100)

def unpickle(file):
    fo = open(file, "rb")
    dict = pickle.load(fo, encoding="latin1")
    fo.close()
    return dict

In [23]:
def conv_layer(input_layer, filters=32, kernel_size=[5,5]):
    # setting up the conv layer, with stride and padding
    return tf.layers.conv2d(
        inputs=input_layer,
        filters=filters,
        kernel_size=kernel_size,
        padding="same",
        activation=tf.nn.relu
    )

def maxpool_layer(conv, pool_size=[2,2], strides=2):
    return tf.layers.max_pooling2d(
        inputs=conv, pool_size=pool_size, strides=strides
    )

def dropout_layer(inputs, mode, rate=0.25):
    
    return tf.layers.dropout(
        inputs=inputs, rate=rate, training=mode == learn.ModeKeys.TRAIN
    )

def dense_layer(inputs, units, activation=tf.nn.relu):
    return tf.layers.dense(inputs=inputs, units=units, activation=activation)

def determine_loss(labels, logits, mode):
    print(mode)
#     if mode != learn.ModeKeys.INFER:
        return tf.losses.softmax_cross_entropy (
            onehot_labels=one_hot_labels(labels),
            logits=logits
        )
#     else:
#         return None
    
def determine_train_op(loss, mode):
    print(mode)
#     if mode == learn.ModeKeys.TRAIN:
        return tf.contrib.layers.optimize_loss (
            loss=loss, 
            global_step=tf.contrib.framework.get_global_step(),
            learning_rate=0.0001,
            optimizer="Adam"
        )
#     else:
#         return None
    
def generate_predictions(logits):
    return {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

def cnn_model(features, labels, mode): 
    mode = learn.ModeKeys.TRAIN if mode == "train" else learn.ModeKeys.INFER
    input_layer = tf.convert_to_tensor(features)
    
    # cnn layer 1
    conv1 = conv_layer(input_layer)
    conv2 = conv_layer(conv1)
    
    # pooling layer 1 
    pool1 = maxpool_layer(conv2)
    
    # dropout operation
    dropout1 = dropout_layer(pool1, mode)
    
    # cnn layer 2 
    conv3 = conv_layer(dropout1, 64, [3, 3])
    conv4 = conv_layer(conv3, 64, [3, 3])
    
    # pooling layer 2
    pool2 = maxpool_layer(conv4)
    
    # dropout operation
    dropout2 = dropout_layer(pool2, mode)
    
    # flatten tensor into a batch of vectors
    pool2_flat = tf.reshape(dropout2, [-1, 8 * 8 * 64])
    
    # dense layer 
    dense1 = dense_layer(pool2_flat, 1024)
    
    # flatten tensor again
    dropout3 = dropout_layer(dense1, mode, 0.4)
    
    # second fully connected layer 
    dense2 = tf.layers.dense(inputs=dropout3, units=512)
    
    # dropout operation
    dropout4 = dropout_layer(dense2, mode, 0.4)
    
    # logits layer
    logits = tf.layers.dense(inputs=dropout4, units=100)
    
    loss = determine_loss(labels, logits, mode)
    train_op = determine_train_op(loss, mode)
    predictions = generate_predictions(logits)
    
    return model_fn_lib.ModelFnOps(
        mode=mode, predictions=predictions, loss=loss, train_op=train_op
    )
    

In [24]:
def generate_accuracy_metric():
    # configure the accuracy metric
    return {
        "accuracy": learn.MetricSpec (
            metric_fn=tf.metrics.accuracy, prediction_key="classes"
        )
    }

def print_evaluate_model(cifar_classifier, data, labels, epoches, subset):
    small_train = np.array_split(data, epoches)[subset]
    small_labels = np.array_split(labels, epoches)[subset]
    evaluate_results = cifar_classifier.evaluate(
        x=small_train, y=small_labels, metrics=generate_accuracy_metric()
    )
    print(evaluate_results)
    return evaluate_results

def serving_input_receiver_fn():
    serialized_tf_example = tf.placeholder(dtype=tf.string, shape=[None], name="input_tensors")
    

def setup_and_train_model():
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/train")
    data = dataset["data"]
    data = data.astype("float32")
    train_data = convert_input_format(data)
    train_labels = convert_output_labels(dataset)
    model_ckpt = "/tmp/cifar100"
    
    # create custom estimator
    cifar_classifier = learn.Estimator (
        model_fn=cnn_model, model_dir="/tmp/cifar100" 
    )
    
    # log predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook (
        tensors=tensors_to_log, every_n_iter=100
    )
    
    # train the model
    with tf.device("/cpu:0"):
        cifar_classifier.fit (
            x=train_data,
            y=train_labels,
            batch_size=64, 
            steps=5240,
            monitors=[logging_hook]
        )
    
#     full_model_dir = cifar_classifier.export_savedmodel(
#         export_dir_base="./models/cifar-100"
#     )
    return cifar_classifier


def test_model(cifar_classifier):
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/test")
    data = dataset["data"]
    data = data.astype("float32")
    test_data = convert_input_format(data)
    test_labels = convert_output_labels(dataset)
    
    # evaluate all test data and print results
    acc = 0
    e_loss = 0
    n_batches = 20
    for i in range (0, n_batches - 1):
        small_eval =  np.array_split(test_data, n_batches)[i]
        small_labs =  np.array_split(test_labels, n_batches)[i]
        eval_results = cifar_classifier.evaluate(
          x=small_eval, y=small_labs, metrics=generate_accuracy_metric())
        print(eval_results)
        acc += eval_results["accuracy"]
        e_loss += eval_results["loss"]

    overall_acc = acc / n_batches
    overall_loss = e_loss/ n_batches
    print("Eval Accuracy = ", overall_acc)
    print("Eval Loss = ", overall_loss) 

In [13]:
classifier = setup_and_train_model()

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_session_config': None, '_keep_checkpoint_max': 5, '_num_worker_replicas': 0, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x16b7cc390>, '_master': '', '_tf_random_seed': None, '_keep_checkpoint_every_n_hours': 10000, '_device_fn': None, '_num_ps_replicas': 0, '_save_checkpoints_secs': 600, '_train_distribute': None, '_environment': 'local', '_model_dir': '/tmp/cifar100', '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_task_id': 0, '_evaluation_master': '', '_log_step_count_steps': 100, '_is_chief': True, '_task_type': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-20090
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Saving checkpoints for 2009

INFO:tensorflow:loss = 1.5734171, step = 20091
INFO:tensorflow:global_step/sec: 2.5192
INFO:tensorflow:probabilities = [[0.00002955 0.00004414 0.02040478 0.00020517 0.00042486 0.0007342
  0.00035214 0.00000618 0.0001278  0.00056609 0.00001504 0.16838115
  0.00485633 0.0001089  0.00003169 0.00092181 0.00654668 0.00023719
  0.00045615 0.00031093 0.00009927 0.00357559 0.0004781  0.00142401
  0.00010964 0.00021655 0.00002543 0.00000942 0.00010749 0.00060477
  0.00006895 0.0019908  0.00371024 0.00013957 0.00027948 0.15643586
  0.00045804 0.00009922 0.00009405 0.00005885 0.00989255 0.00000652
  0.00003847 0.00051047 0.00006886 0.00018618 0.30397418 0.00001239
  0.00005987 0.00052578 0.0001727  0.00038376 0.00000232 0.0001189
  0.00079391 0.00052711 0.00110442 0.00026149 0.00004652 0.00031358
  0.00003202 0.00007277 0.00009249 0.00000975 0.0004876  0.0002011
  0.00006857 0.00005776 0.00006127 0.0003512  0.00010833 0.00086922
  0.00010317 0.0001668  0.00010938 0.0000311  0.00490957 0.00014179


INFO:tensorflow:loss = 1.6209886, step = 20191 (39.697 sec)
INFO:tensorflow:global_step/sec: 2.24279
INFO:tensorflow:probabilities = [[0.00011873 0.01622931 0.00050624 0.00240619 0.00285423 0.00020165
  0.18368122 0.04528661 0.00089774 0.00027652 0.00020961 0.00034056
  0.00762135 0.00063943 0.12509282 0.00338351 0.00005757 0.00037924
  0.08833691 0.00639396 0.00006086 0.00006455 0.00016327 0.00011761
  0.00575395 0.00010258 0.09741365 0.00721147 0.00007705 0.01400136
  0.00063313 0.00028298 0.00324617 0.00156671 0.00531189 0.00006051
  0.00019432 0.00266079 0.00048157 0.00152664 0.00009786 0.00303316
  0.0016458  0.00046856 0.02681565 0.1128983  0.00038493 0.00172897
  0.0033796  0.00100247 0.00081007 0.00328801 0.00047317 0.0087044
  0.00086195 0.00217412 0.00755973 0.00438461 0.00166075 0.00069933
  0.00015484 0.00008335 0.00537169 0.00007939 0.00208256 0.0000274
  0.00003588 0.00372353 0.00042788 0.00123196 0.00158052 0.00014266
  0.01701315 0.00047227 0.00130847 0.00287149 0.00002

INFO:tensorflow:loss = 1.9536054, step = 20291 (44.608 sec)
INFO:tensorflow:global_step/sec: 2.41004
INFO:tensorflow:probabilities = [[0.00040865 0.04590222 0.00019351 0.00001078 0.00001244 0.5892138
  0.00000157 0.00004712 0.00000629 0.0151951  0.00415016 0.0041586
  0.00070077 0.01362317 0.00007833 0.0000104  0.04231361 0.00051579
  0.000211   0.00004712 0.00002484 0.00028663 0.00340098 0.00004796
  0.00000385 0.00852618 0.00000288 0.00024028 0.00010768 0.00000034
  0.00002263 0.0000078  0.00806892 0.00003904 0.00000466 0.00030892
  0.00001042 0.00011334 0.00000685 0.00057617 0.00046012 0.00013975
  0.0000009  0.00000467 0.00002866 0.00005772 0.00271644 0.00003553
  0.00012709 0.00000667 0.00002959 0.00009301 0.00000148 0.00017461
  0.00007779 0.00010822 0.0000018  0.00022468 0.00648367 0.00001624
  0.00002209 0.00269115 0.0010267  0.00000083 0.00002912 0.00011478
  0.00001397 0.00001522 0.00007777 0.00028475 0.00008012 0.00042679
  0.00013682 0.0001279  0.00001394 0.00000167 0.00033

INFO:tensorflow:loss = 1.7277961, step = 20391 (41.573 sec)
INFO:tensorflow:global_step/sec: 2.40837
INFO:tensorflow:probabilities = [[0.00000023 0.         0.         0.         0.         0.00000106
  0.00000002 0.0000007  0.         0.9995295  0.00000013 0.00000001
  0.         0.         0.00000002 0.         0.00015161 0.
  0.00000004 0.         0.00000146 0.         0.00000026 0.
  0.00001218 0.00000018 0.         0.         0.00000005 0.
  0.         0.         0.         0.         0.         0.00000001
  0.         0.         0.         0.00000002 0.00006266 0.00000003
  0.         0.         0.         0.00000001 0.00000005 0.
  0.         0.         0.         0.         0.         0.00000268
  0.00000009 0.         0.00000021 0.00018059 0.         0.
  0.         0.00000002 0.         0.         0.         0.
  0.         0.         0.         0.00000091 0.         0.00000004
  0.         0.         0.         0.         0.00000023 0.
  0.00000009 0.00000033 0.         0.  

...

INFO:tensorflow:loss = 1.5680135, step = 24891 (37.451 sec)
INFO:tensorflow:global_step/sec: 2.68969
INFO:tensorflow:probabilities = [[0.         0.00000013 0.00000003 0.00000059 0.00000001 0.00000001
  0.         0.00000002 0.         0.00000001 0.         0.
  0.00010107 0.00000033 0.         0.00000001 0.00000003 0.
  0.         0.00000005 0.00000001 0.00000246 0.00000001 0.00000077
  0.00000001 0.00000002 0.00000001 0.00000003 0.00000003 0.00000001
  0.01103728 0.00000002 0.00000109 0.         0.         0.
  0.         0.         0.         0.00000001 0.00000163 0.
  0.         0.         0.         0.00000005 0.00000036 0.
  0.00000007 0.00002426 0.         0.         0.         0.
  0.         0.00002286 0.00000013 0.         0.0000099  0.00000008
  0.00000006 0.         0.00000006 0.         0.         0.00000024
  0.         0.000002   0.0000198  0.00000533 0.00000002 0.00007548
  0.00003526 0.00276986 0.         0.00000066 0.00000418 0.
  0.         0.         0.         0.  

INFO:tensorflow:loss = 1.4850612, step = 24991 (37.178 sec)
INFO:tensorflow:global_step/sec: 2.59753
INFO:tensorflow:probabilities = [[0.         0.00000023 0.00000008 0.00001628 0.0000008  0.00000026
  0.00000011 0.00000035 0.00000016 0.00000032 0.00000001 0.00000002
  0.00002974 0.0000009  0.00000002 0.00000037 0.00000014 0.00000118
  0.00000095 0.00000019 0.00000003 0.00000002 0.00000008 0.00003413
  0.0000023  0.         0.00000032 0.00000072 0.0000002  0.0000122
  0.90406    0.00000021 0.00003722 0.00000039 0.00000007 0.00000022
  0.00000001 0.00000007 0.00000743 0.00000403 0.00003305 0.00000001
  0.00000002 0.00000001 0.00000045 0.00000024 0.00000012 0.00000006
  0.00000002 0.00003123 0.00000094 0.00000002 0.00000041 0.00000001
  0.00000017 0.0000657  0.00127175 0.00000018 0.00000018 0.00004453
  0.00000096 0.00000002 0.00000009 0.00000045 0.00000207 0.00000262
  0.00000221 0.00001403 0.00000045 0.00038938 0.00000006 0.00004433
  0.00011432 0.00066469 0.00000005 0.00000057 0.0004

INFO:tensorflow:loss = 1.5729983, step = 25091 (38.499 sec)
INFO:tensorflow:global_step/sec: 2.70003
INFO:tensorflow:probabilities = [[0.00046177 0.00001317 0.00011644 0.00000584 0.00000078 0.00364522
  0.00001559 0.00005513 0.00000086 0.00027712 0.47385544 0.0001186
  0.00000114 0.00000485 0.00001096 0.00003245 0.11471502 0.00000029
  0.00004773 0.00010176 0.01246181 0.00000065 0.00058731 0.00010048
  0.00334861 0.0124868  0.00009816 0.00000331 0.3247134  0.00000327
  0.00000617 0.00000163 0.0000044  0.00000203 0.00002158 0.00000914
  0.00051636 0.0000024  0.00000185 0.00024988 0.01153142 0.00000044
  0.00000364 0.00000652 0.00217566 0.00008809 0.0000469  0.00000079
  0.00000021 0.00000171 0.00004965 0.00083881 0.00000018 0.00060023
  0.00099593 0.0000298  0.00000004 0.00001009 0.00001214 0.00000044
  0.00007034 0.00549682 0.00001015 0.00000187 0.00000397 0.00002178
  0.00000199 0.00017606 0.00002904 0.00065021 0.00003884 0.00032699
  0.0000075  0.00003771 0.00001073 0.00000951 0.0000

INFO:tensorflow:loss = 1.8347888, step = 25191 (37.037 sec)
INFO:tensorflow:global_step/sec: 2.61742
INFO:tensorflow:probabilities = [[0.00045373 0.00294944 0.00811702 0.01603977 0.02321906 0.00195709
  0.00361304 0.02409403 0.00233078 0.00042256 0.00463424 0.00139426
  0.00209859 0.00155673 0.00975879 0.00312549 0.00212263 0.00034609
  0.01015882 0.00445451 0.00105877 0.03072413 0.0012722  0.00069614
  0.00704869 0.00125081 0.0098265  0.04152981 0.00123703 0.00991853
  0.00376454 0.02226854 0.00809178 0.00074101 0.00346766 0.00477151
  0.00331243 0.00216984 0.03408791 0.0026657  0.00280968 0.00169869
  0.00744817 0.00516521 0.02502572 0.00360058 0.00881277 0.0002865
  0.00248757 0.00052263 0.00879111 0.01598448 0.00077182 0.000783
  0.00122751 0.03671565 0.00091291 0.00106898 0.00256378 0.0010167
  0.00059117 0.00263952 0.00040566 0.02104237 0.20819245 0.00926048
  0.03728388 0.00485928 0.00104305 0.0005988  0.00070255 0.00052887
  0.03294706 0.00428123 0.02862169 0.02650737 0.0002633

INFO:tensorflow:loss = 1.6034079, step = 25291 (38.205 sec)
INFO:tensorflow:Saving checkpoints for 25330 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:Loss for final step: 1.8500407.


In [22]:
test_model(classifier)

ValueError: None values not supported.